
# 高斯混合模型椭圆体

绘制通过期望最大化（ ``GaussianMixture`` 类）和变分推断（具有狄利克雷过程先验的 ``BayesianGaussianMixture`` 类模型）获得的两个高斯混合模型的置信椭圆体。

两个模型都可以使用五个组件来拟合数据。请注意，期望最大化模型将必然使用所有五个组件，而变分推断模型实际上只会使用所需的组件数量以获得良好的拟合。在这里我们可以看到，期望最大化模型会任意地分割一些组件，因为它试图拟合过多的组件，而狄利克雷过程模型会自动调整其状态数量。

这个例子没有展示出来，因为我们处于低维空间中，但狄利克雷过程模型的另一个优点是，即使每个簇的示例数量少于数据的维度，由于推断算法的正则化特性，它也可以有效地拟合完整的协方差矩阵。


In [ ]:
import itertools

import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
from scipy import linalg

from sklearn import mixture

color_iter = itertools.cycle(["navy", "c", "cornflowerblue", "gold", "darkorange"])


def plot_results(X, Y_, means, covariances, index, title):
    splot = plt.subplot(2, 1, 1 + index)
    for i, (mean, covar, color) in enumerate(zip(means, covariances, color_iter)):
        v, w = linalg.eigh(covar)
        v = 2.0 * np.sqrt(2.0) * np.sqrt(v)
        u = w[0] / linalg.norm(w[0])
        # 由于动态规划不会使用它能访问的每个组件，除非它需要它们，我们不应该绘制冗余组件。
        if not np.any(Y_ == i):
            continue
        plt.scatter(X[Y_ == i, 0], X[Y_ == i, 1], 0.8, color=color)

        # 绘制椭圆以显示高斯成分
        angle = np.arctan(u[1] / u[0])
        angle = 180.0 * angle / np.pi  # convert to degrees
        ell = mpl.patches.Ellipse(mean, v[0], v[1], angle=180.0 + angle, color=color)
        ell.set_clip_box(splot.bbox)
        ell.set_alpha(0.5)
        splot.add_artist(ell)

    plt.xlim(-9.0, 5.0)
    plt.ylim(-3.0, 6.0)
    plt.xticks(())
    plt.yticks(())
    plt.title(title)


# Number of samples per component
# 
# 
n_samples = 500

# 生成随机样本，两个组成部分
np.random.seed(0)
C = np.array([[0.0, -0.1], [1.7, 0.4]])
X = np.r_[
    np.dot(np.random.randn(n_samples, 2), C),
    0.7 * np.random.randn(n_samples, 2) + np.array([-6, 3]),
]

# 使用五个成分通过EM拟合高斯混合模型
gmm = mixture.GaussianMixture(n_components=5, covariance_type="full").fit(X)
plot_results(X, gmm.predict(X), gmm.means_, gmm.covariances_, 0, "Gaussian Mixture")

# 使用五个成分拟合狄利克雷过程高斯混合模型
dpgmm = mixture.BayesianGaussianMixture(n_components=5, covariance_type="full").fit(X)
plot_results(
    X,
    dpgmm.predict(X),
    dpgmm.means_,
    dpgmm.covariances_,
    1,
    "Bayesian Gaussian Mixture with a Dirichlet process prior",
)

plt.show()